In [1]:
!node --version

v14.18.0


In [2]:
import sys
sys.path.append("/Users/alexandrec/Kaggle/simple")

import os
os.getcwd() 

'/Users/alexandrec/lux-ai-2021/Kaggle/simple'

In [3]:
!pip install kaggle-environments -U
!pip install torch

You should consider upgrading via the '/Users/alexandrec/jupyter-env/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/Users/alexandrec/jupyter-env/bin/python -m pip install --upgrade pip' command.


In [4]:
from kaggle_environments import make
import numpy as np
import torch

Loading environment football failed: No module named 'gfootball'


In [5]:
env = make("lux_ai_2021", configuration={"seed": 562124210, "loglevel": 2, "annotations": True}, debug=True)


In [6]:
import torch
import copy
class MapEncoder(torch.nn.Module):
    def __init__(self):
        super().__init__()
        self.conv1 = torch.nn.Conv2d(10, 64, 8, 2)
        self.conv2 = torch.nn.Conv2d(64, 128, 4, 2)
        self.relu = torch.nn.ReLU()
        self.ffn_map = torch.nn.Linear(3200,512)
    def forward(self, x):
        y = self.conv1(x)
        y = self.relu(y)
        y = self.conv2(y)
        y = self.relu(y)
        flat = y.view(-1, 3200)
        out = self.ffn_map(flat)
        return out

class LuxrNet(torch.nn.Module):
    def __init__(self, output_dim):
        super().__init__()
        self.rnn = torch.nn.GRU(8, 128, 2, dropout=0)
        self.mapEncoder = MapEncoder()
        self.relu = torch.nn.ReLU()
        self.joiner = torch.nn.Linear(640,512)
        self.output = torch.nn.Linear(512,output_dim)

    def forward(self, global_features, units_features):
        seq_len = units_features.shape[1]
        hk = torch.zeros(2, seq_len, 128)
        glob = self.mapEncoder(global_features)
        preds, hn = self.rnn(units_features, hk)
        hidden_out = self.joiner(torch.cat((glob.repeat(1,seq_len,1), preds), 2))
        out = self.output(self.relu(hidden_out))
        return [out[:,k,:] for k in range(seq_len)]

class DDQN(torch.nn.Module):
    def __init__(self, output_dim):
        super().__init__()
        self.online = LuxrNet(output_dim)
        self.target = copy.deepcopy(self.online)
        
        for p in self.target.parameters():
            p.requires_grad = False

    def forward(self, state, mode):
        global_features = state[0]
        units_features = state[1]
        if mode == "online":
            return self.online(global_features, units_features)
        if mode == "target":
            return self.target(global_features, units_features)
   

t = torch.rand(1, 10, 32, 32)
t2 = torch.rand(1, 12, 8)
print(t2[:,0,:].dtype)

model = DDQN(8)
y = model([t,t2],"online")
print(y)




torch.float32
[tensor([[-0.0199,  0.0161, -0.0152, -0.0231, -0.0481, -0.0094,  0.0162,  0.0414]],
       grad_fn=<SliceBackward>), tensor([[-0.0202,  0.0176, -0.0152, -0.0243, -0.0495, -0.0083,  0.0173,  0.0413]],
       grad_fn=<SliceBackward>), tensor([[-0.0191,  0.0175, -0.0143, -0.0231, -0.0482, -0.0089,  0.0173,  0.0415]],
       grad_fn=<SliceBackward>), tensor([[-0.0187,  0.0155, -0.0136, -0.0229, -0.0479, -0.0100,  0.0162,  0.0421]],
       grad_fn=<SliceBackward>), tensor([[-0.0186,  0.0164, -0.0143, -0.0233, -0.0478, -0.0090,  0.0173,  0.0408]],
       grad_fn=<SliceBackward>), tensor([[-0.0194,  0.0165, -0.0152, -0.0229, -0.0493, -0.0099,  0.0165,  0.0419]],
       grad_fn=<SliceBackward>), tensor([[-0.0190,  0.0180, -0.0145, -0.0236, -0.0492, -0.0085,  0.0179,  0.0413]],
       grad_fn=<SliceBackward>), tensor([[-0.0198,  0.0173, -0.0146, -0.0234, -0.0480, -0.0088,  0.0167,  0.0413]],
       grad_fn=<SliceBackward>), tensor([[-0.0183,  0.0167, -0.0139, -0.0229, -0.0485, -0.

In [7]:
# optimizer.zero_grad()        
# loss, hidden = model(data, hidden, targets)
# loss.backward()

# torch.nn.utils.clip_grad_norm(model.parameters(), args.clip)
# optimizer.step()

In [9]:
# wrapper for observation preprocessing - features extraction from the game
import math, sys
from lux.game import Game
from lux.game_map import Cell, RESOURCE_TYPES
from lux.constants import Constants
from lux.game_constants import GAME_CONSTANTS
from lux import annotate

import torch
import numpy as np

# test agent 
from agent import agent

class EnvWrapper:
    def __init__(self, env, opponent):
        self.game_state = Game()
        self.env = env
        self.trainer = env.train([None,opponent])
        obs = self.trainer.reset()
        self.update_game_state(obs)


    def update_game_state(self, observation):
        """Update the local game state from observation"""

        if observation["step"] == 0:
            self.game_state = Game()
            self.game_state._initialize(observation["updates"])
            self.game_state._update(observation["updates"][2:])
            self.game_state.id = observation.player
        else:
            self.game_state._update(observation["updates"])
        self.obs = observation
        self.game_map = self.game_state.map
        self.player = self.game_state.players[observation.player]
        self.opponent = self.game_state.players[(observation.player + 1) % 2]
        self.width, self.height = self.game_map.width, self.game_map.height

        self.resource_tiles: list[Cell] = []
        self.city_tiles: list[Cell] = []
    
        for y in range(self.height):
            for x in range(self.width):
                cell = self.game_state.map.get_cell(x, y)
                if cell.has_resource():
                    self.resource_tiles.append(cell)
                if cell.citytile is not None:
                    self.city_tiles.append(cell)   

        return self.game_state
    
    def get_reward(self):
        """Workaround to get a correct reward"""
        player = self.player
        ct_count = sum([len(v.citytiles) for k, v in player.cities.items()])
        unit_count = len(self.game_state.players[player.team].units)
        return ct_count * 10000 + unit_count*100 + self.obs["step"]*10
    

    def get_cell_resources(self, cell: Cell):
        wood = 0
        coal = 0
        uranium = 0
        if cell.has_resource():
            wood = cell.resource.amount if cell.resource.type == "wood" else 0
            coal = cell.resource.amount if cell.resource.type == 'coal' else 0
            uranium = cell.resource.amount if cell.resource.type == 'uranium' else 0
        return wood, coal, uranium
    
    def get_adjacent_resources(self, pos):
        wood = 0
        coal = 0
        uranium = 0
        x, y = (pos.x, pos.y)
        for i in range(-1,1):
            for j in range(-1,1):
                cell = self.game_map.get_cell(x+i,y+j)
                if cell.has_resource():
                    wood += cell.resource.amount if cell.resource.type == "wood" else 0
                    coal += cell.resource.amount if cell.resource.type == 'coal' else 0
                    uranium += cell.resource.amount if cell.resource.type == 'uranium' else 0
        return wood, coal, uranium
    
    def get_units_state(self):
        units = []
        for unit in self.player.units:
            if unit.can_act():
                cell = self.game_map.get_cell_by_pos(unit.pos)
                worker_type = 0 if unit.is_worker() else 1
                cargo = unit.get_cargo_space_left()
                pos_x = unit.pos.x
                pos_y = unit.pos.y
                is_in_city = cell.citytile != None
                adjacent_wood, adjacent_coal, adjacent_uranium = self.get_adjacent_resources(unit.pos)
                units.append([worker_type, cargo, adjacent_wood, adjacent_coal, adjacent_uranium, is_in_city, pos_x, pos_y])
        return torch.tensor(units,dtype=torch.float32)       
    
    def get_cell_type(self, cell):
        cell_code = 0
        all_units = [self.player.units, self.opponent.units]
        for unit in self.player.units:
            if unit.pos == cell.pos:
                cell_code = 1
                if unit.is_cart:
                    cell_code +=0.5
        for unit in self.opponent.units:
            if unit.pos == cell.pos:
                cell_code = 2
                if unit.is_cart:
                    cell_code +=0.5
        return cell_code


    def get_global_state(self):
        state = torch.zeros(10,32,32, dtype=torch.float32)
        for x in range(self.width):
            for y in range(self.height):
                cell = self.game_map.get_cell(x,y)
                w, c, u = self.get_cell_resources(cell)
                cell_occupant = self.get_cell_type(cell)
                cityid = int(cell.citytile.cityid[2:])+1 if cell.citytile else 0
                city = (cell.citytile.team+1) if cell.citytile else 0
                fuel = (self.opponent.cities[cell.citytile.cityid].fuel if city == self.opponent.team+1
                       else self.player.cities[cell.citytile.cityid].fuel if city == self.player.team+1 else 0)
                road = cell.road
                state[:,x,y]= torch.tensor([w, c, u, cell_occupant, cityid, fuel, city, road, x, y])
        return state


    def step(self, action):
        obs, _, done, info = self.trainer.step(action)
        game_state = self.update_game_state(obs)
        reward = self.get_reward()
        global_state = self.get_global_state()
        units_state = self.get_units_state()
        city_state = torch.tensor([])
        return [global_state,units_state,city_state], reward, done, info

    def reset(self):
        obs = self.trainer.reset()
        self.update_game_state(obs)
        global_state = self.get_global_state()
        units_state = self.get_units_state()
        city_state = torch.tensor([])
        return [global_state,units_state,city_state]
    
    def get_game_objects(self):
        return [self.player, self.city_tiles]
    
#TEST
env = make("lux_ai_2021", configuration={"seed": 562124210, "loglevel": 2, "annotations": True}, debug=True)
print(env.reset())
env = EnvWrapper(env, agent)
state = env.reset()

game_objects = env.get_game_objects()

[{'action': [], 'reward': 0, 'info': {}, 'observation': {'remainingOverageTime': 60, 'step': 0, 'width': 32, 'height': 32, 'reward': 0, 'globalUnitIDCount': 2, 'globalCityIDCount': 2, 'player': 0, 'updates': ['0', '32 32', 'rp 0 0', 'rp 1 0', 'r wood 0 29 316', 'r wood 1 24 342', 'r wood 1 25 323', 'r uranium 1 31 332', 'r wood 2 24 329', 'r wood 2 25 397', 'r wood 2 26 364', 'r uranium 2 31 346', 'r wood 3 28 800', 'r wood 4 10 318', 'r wood 4 11 398', 'r uranium 4 17 336', 'r wood 4 27 800', 'r wood 4 28 800', 'r wood 5 10 308', 'r wood 5 11 326', 'r uranium 5 17 335', 'r coal 7 31 355', 'r coal 8 0 369', 'r coal 8 30 404', 'r coal 8 31 422', 'r wood 11 23 317', 'r wood 11 24 330', 'r wood 11 25 314', 'r wood 12 23 349', 'r wood 12 24 390', 'r wood 13 6 337', 'r wood 13 7 325', 'r wood 13 24 374', 'r wood 14 6 369', 'r wood 14 7 387', 'r coal 14 16 393', 'r coal 15 14 379', 'r coal 15 15 411', 'r coal 15 16 403', 'r coal 16 14 379', 'r coal 16 15 411', 'r coal 16 16 403', 'r wood 17 

In [10]:
import random
import sys
from lux.game import Game
from functools import partial
from collections import deque
from lux.constants import Constants
from torch.autograd import Variable

DIRECTIONS = Constants.DIRECTIONS
class Bot:
    def __init__(self, save_dir):
        
        self.use_cuda = torch.cuda.is_available()
        self.save_dir = save_dir
        self.action_space = 6
        self.model = DDQN(self.action_space)
        self.memory = deque(maxlen=100000)
        
        self.exploration_rate = 1
        self.exploration_rate_decay = 0.99999975
        self.exploration_rate_min = 0.1
        self.curr_step = 0
        self.save_every = 5e5
        self.batch_size = 1
        self.gamma = 0.9

        self.optimizer = torch.optim.Adam(self.model.parameters(), lr=0.00025)
        self.loss_fn = torch.nn.SmoothL1Loss()
        
        self.burnin = 7000 #1e4  # min. experiences before training
        self.learn_every = 2  # no. of experiences between updates to Q_online
        self.sync_every = 1e4  # no. of experiences between Q_target & Q_online sync
        
        self.log_every = 30

        # if self.use_cuda:
        #     self.net = self.net.to(device="cuda")

    def play(self, state, game_objects):
        """Play 1 step with epsilon-greedy policy and return actions"""
        actions = []
        player, city_tiles = game_objects
        global_state_tensor = state[0].unsqueeze(0)
        units_state_tensor = state[1].unsqueeze(0)
        explore = np.random.rand() < self.exploration_rate

        def get_random_actions(unit):
            actions_list = [unit.move(DIRECTIONS.NORTH), unit.move(DIRECTIONS.SOUTH), unit.move(DIRECTIONS.EAST), 
                            unit.move(DIRECTIONS.WEST), unit.build_city(), unit.pillage()]
            i = np.random.randint(6, size=1)[0]
            return actions_list[i]

        # TODO: pad if map size < 32

        for citytile in city_tiles:
            # TODO: hardcoded city policy here
            pass

        # print(player.team)
        if (explore):
        #EXPLORE
            for unit in player.units:
                if unit.is_worker() and unit.can_act():
                    actions.append(get_random_actions(unit))
        else:
        # EXPLOIT
            if len(units_state_tensor) > 1:
                action_qvalues = self.model([global_state_tensor, units_state_tensor], mode="online")
                # print(action_qvalues)
                # select idx with higher Q prediction for each unit
                action_idx = [torch.argmax(Q, axis=1).item() for Q in action_qvalues]

                idx=0
                for unit in player.units:
                    if unit.can_act():
                        actions_list = [unit.move(DIRECTIONS.NORTH), unit.move(DIRECTIONS.SOUTH), unit.move(DIRECTIONS.EAST), 
                                unit.move(DIRECTIONS.WEST), unit.build_city(), unit.pillage()]
                        action = actions_list[action_idx[idx]]
                        actions.append(action)
                        idx+=1

        # decrease exploration_rate
        self.exploration_rate *= self.exploration_rate_decay
        self.exploration_rate = max(self.exploration_rate_min, self.exploration_rate)

        # increment step
        self.curr_step += 1

        return actions

    def cache(self, state, next_state, action, reward, done, info):
        global_state = state[0]
        units_state = state[1]
        
        next_global_state = next_state[0]
        next_unit_state = next_state[1]
        
        action = torch.tensor(action)
        reward = torch.tensor([reward])
        done = torch.tensor([done])

        self.memory.append((global_state, units_state, next_global_state, next_unit_state, action, reward, done,))
    
    def get_batch(self):
        """Sample a batch from the cache"""
        batch = random.sample(self.memory, self.batch_size)
        global_state, units_state, next_global_state, next_unit_state, action, reward, done = map(torch.stack, zip(*batch))
        return global_state, units_state, next_global_state, next_unit_state, action, reward.squeeze(), done.squeeze()
    
    def save(self):
        save_path = (
            self.save_dir / f"LuxRN_net_{int(self.curr_step // self.save_every)}.chkpt"
        )
        torch.save(
            dict(model=self.model.state_dict(), exploration_rate=self.exploration_rate),
            save_path,
        )
        print(f"LuxRN saved to {save_path} at step {self.curr_step}")

    def learn(self):
        # Only work with batch-size 1 so far

        def td_estimate(state, actions):
            """Estimate for a sequence of units"""
            Q_sequence = self.model(state, mode="online")
            current_Q_sequence = [current_Q[:, action] for current_Q, action in zip (Q_sequence, actions)]
            return current_Q_sequence

        @torch.no_grad()
        def td_target(reward, next_state, done):
            """Target for a sequence of units"""
            next_state_Q_sequence = self.model(next_state, mode="online")
            best_actions = [torch.argmax(next_state_Q, axis=1) for next_state_Q in next_state_Q_sequence]
            next_Q_sequence = self.model(next_state, mode="target")
            next_best_Q_sequence = [next_Q[:,action] for next_Q, action in zip (next_Q_sequence, best_actions)]
            return [(reward + (1 - done.float()) * self.gamma * next_Q).float() for next_Q in next_best_Q_sequence]
        
        
        def update_Q_online(td_estimate, td_target):
            loss = torch.mean(torch.tensor([self.loss_fn(td_e, td_t) for (td_e, td_t) in zip(td_estimate, td_target)]))
            loss = Variable(loss, requires_grad = True)
            self.optimizer.zero_grad()
            loss.backward()
            self.optimizer.step()
            return loss.item()

        def sync_Q_target():
            self.model.target.load_state_dict(self.model.online.state_dict())
            
            
        if self.curr_step % self.sync_every == 0:
            sync_Q_target()

        if self.curr_step % self.save_every == 0:
            self.save()

        if self.curr_step < self.burnin:
            return None, None
        
        if self.curr_step == self.burnin:
            print("Learning started")
        

        if self.curr_step % self.learn_every != 0:
            return None, None
        
        # Sample from memory
        global_state, units_state, next_global_state, next_unit_state, action, reward, done = self.get_batch()
        state = [global_state, units_state]
        next_state = [next_global_state, next_unit_state]
        
        # Get TD Estimate
        td_est = td_estimate(state, action)

        # Get TD Target
        td_tgt = td_target(reward, next_state, done)

        # Backpropagate loss through Q_online
        loss = update_Q_online(td_est, td_tgt)

        # return (td_est.mean().item(), loss)
        return loss

    def logging(self, to_log):
        # if self.curr_step % self.log_every == 0:
        for (k,v) in to_log.items():
            print(k, v)
            sys.stdout.flush()
        
        

bot = Bot( "./")
bot.play(state, game_objects)




['p u_1']

In [11]:
episodes = 1000
bot = Bot( "./")
env = make("lux_ai_2021", configuration={"seed": 562124210, "loglevel": 2, "annotations": True}, debug=False)
env = EnvWrapper(env, agent)

def action_string_to_idx(action):
    offsets = {"n":0, "s":1, "e":2, "w":3, "b":4, "p":5}
    if action[0] == "m":
        return offsets[action[-1]]
    else:
        return offsets[action[0]]
    

for e in range (episodes):
    state = env.reset()
    game_objects = env.get_game_objects()
    while True:
        # Run agent on the state
        action = bot.play(state, game_objects)
        # print(len(game_objects[0].units))
        # print(action)
        
        # Agent performs action
        next_state, reward, done, info = env.step(action)
        game_objects = env.get_game_objects()
        
        # Remember if action is not empty and next state has units that can play
        if len(action)>0 and len(next_state[1])>0:
            action = [action_string_to_idx(action[0])]
            bot.cache(state, next_state, action, reward, done, info)

        # Learn
        loss = bot.learn()
        
        # Log
        

        # Update state
        state = next_state
        if done:
            bot.logging({"episode":e, "reward": reward})
            break

episode 0
reward 0
episode 1
reward 0
episode 2
reward 0
episode 3
reward 0


KeyboardInterrupt: 

In [15]:
env.env.render(mode="ipython", width=1200, height=800)

In [ ]:
batch_size = 5

In [ ]:

# env.render(mode="ipython", width=1200, height=800)

In [ ]:
env.reset()


In [ ]:
from agent import agent

SyntaxError: invalid syntax (3940591257.py, line 1)

In [ ]:
# TODO: allow batching: needs sequence padding... ie need max number of units (can allow it to vary depending on the batch)
# -> need to be done in get_batch() like a custom data loader
# 1. get max lenght sequence
# 2. pad

# Adapt the Q value slicing for a whole batch
